# Final Project

## Imports

In [18]:
# <include-final_project/utils.py>

In [19]:
# <imports>
import numpy as np
import pandas as pd
import plotly.io as pio


from final_project import utils

pd.options.plotting.backend = "plotly"
pio.templates.default = "seaborn"
pio.renderers.default = "notebook_connected+vscode"

## Summary

This is the exploration of a spread trading stategy involving BTCUSDT and BTCUSDT perpetual futures contracts on the [binance exchange](https://www.binance.us/en/home).

### Overview
The basic strategy is to receive the funding rate when it is attractive and taking advantage of the fact the perptual contract and underlying asset prices converge over time as as result of the funding rate. We do this by tracking the funding rate and shorting the perpetual contract and going long the underlying asset when the funding rate is high and closing positions when the funding rate comes back down. If the funding rate goes sufficiently negative, we go long the perpetual contract and short the underlying asset.

### Funding Rate
The perptual futures contract has a funding rate that are periodic payments made to either short or long traders based on the difference in the perpetual futures price and the spot price. When the market is bullish - perpetual futures price greater than the spot price - the funding rate is positive and long traders pay short traders. When it is bearish, the funding rate is negative and short traders pay long traders.

Funding rate payments are made every 8 hours starting at 00:00 UTC and only gets paid if positions are held at the designated time.

The actual rate has two components, an interest rate and a premium. The interest rate is set by the exchange and may change based on market conditions, such as changes in the federal funds rate. The current interest rate is 0.01% per eight hours, which equates to 0.03% per day or 10.8% per year. The premium is determined based on the bid ask spread relative to an index formed from a bucket of prices from major spot market exchanges [need to understand better](https://www.binance.com/en/support/faq/360033525031). At this point, to begin evaluating the strategy, we use the historical funding rates as provided by the exhange, and have on the todo list a fuller understanding of the mechanics of determining the funding rate.

### Liquidation
Both assets are subject to automatic liquidation when collateral = initial collateral + realized and unrealized profits and losses is less than the maintenance margin. Maintenance margin is determined based on position size an leverage. Perpetual futures contracts can be traded with leverage up to 125x. [need to understand better](https://www.binance.com/en/support/faq/360033525271)

### Markets

In [20]:
df_exch = utils.get_exchange_info()
df_exch.loc["BTCUSDT"]

status                                                                  TRADING
baseAsset                                                                   BTC
baseAssetPrecision                                                            8
quoteAsset                                                                 USDT
quotePrecision                                                                8
quoteAssetPrecision                                                           8
baseCommissionPrecision                                                       8
quoteCommissionPrecision                                                      8
orderTypes                    [LIMIT, LIMIT_MAKER, MARKET, STOP_LOSS_LIMIT, ...
icebergAllowed                                                             True
ocoAllowed                                                                 True
quoteOrderQtyMarketAllowed                                                 True
isSpotTradingAllowed                    

## Perpetual Contract

In [21]:
interval = "8h"

In [22]:
df_perpetual = utils.get_continuous_contracts(pair="BTCUSDT", start_time="2020-05-01", interval=interval)

In [23]:
fig = utils.make_price_volume_chart(
    df_perpetual,
    title="BTCUSDT Perpetual Contracts"
)
fig.show()

In [24]:
fig = utils.make_overview_chart(df_perpetual.per_return, title="BTCUSDT Perpetual", subtitle_base="Log Returns")
fig.show()

## Spot Prices

These are the same prices as above.

In [25]:
df_spot = utils.get_klines(symbol="BTCUSDT", start_time="2020-05-01", interval=interval)
fig = utils.make_price_volume_chart(df_spot, title="BTCUSDT Spot Price OHLC")
fig.show()

In [26]:
fig = utils.make_overview_chart(
    df_spot.per_return, title="BTCUSDT Spot",
    subtitle_base="Log Returns"
)
fig.show()

## Funding Rate

It looks like the funding rate rarely goes negative. Is that because the perpetual price rarely goes below the spot price or is there something structural that may present and arbitrage opportunity going on?

In [27]:
df_funding = utils.get_funding_rate_history(symbol="BTCUSDT", start_time="2020-05-01")
fig = df_funding.fundingRate.plot(title="BTCUSDT Funding Rate")
fig.update_traces(line=dict(width=1))
fig.update(layout_showlegend=False)
fig.show()

The cumulative funding rate essentially shows what return would have been generated by opening one trade short the perpetual and long the spot and holding it for the entire period.

In [28]:
fig = utils.make_overview_chart(
    df_funding.fundingRate, title="Funding Rate",
    subtitle_base="Funding Rate"
)
fig.show()

## Spread

This is of the spread itself - the percentage difference between the perpetual and spot prices and excludes a spread outlier on 2020-12-21 of 0.018.

In [29]:
spread = (df_perpetual.close / df_spot.close - 1)
spread.name = "spread"
fig = utils.make_2_yaxis_lines(
    spread[spread.abs() < .015], df_funding.fundingRate,
    title="Perpetual - Spot Spread vs. Funding Rate"
)
fig.show()
# print(f"correlation: {spread[spread.abs() < .015].corr(df_funding.fundingRate):0.4f}")

In [30]:
fig = utils.make_overview_chart(
    spread[spread.abs() < .015],
    title="Perpetual Spot Spread",
    subtitle_base="Spread"
)
fig.show()

This shows that the difference in returns between the perpetual and the spot basically revert to zero over time, which means that there is profit to be made in chasing the funding rate, shorting the perpetual while going long the underlying asset to get the funding rate.

In [31]:
spread = (df_perpetual.per_return - df_spot.per_return).rolling(9).sum()
spread.name = "spread"
fig = utils.make_2_yaxis_lines(
    spread[spread.abs() < .015], df_funding.fundingRate.rolling(9).sum(),
    title="Perpetual - Spot Return Spread vs. Funding Rate"
)
# print(f"correlation: {spread[spread.abs() < .015].corr(df_funding.fundingRate):0.4f}")
fig.show()

## Strategy

This strategy is essentially designed to capture the funding rate, shorting the perpertual and going long the underlying asset when the funding rate is high.

* Evaluates positions every 8 hours
* Trading costs assumed to be 0.05% (average of 0.03% on futures and 0.07% on the underlying asset)
* Conservatively assumes $200,000 in dedicated capital and no leverage

A better strategy would be to simply hold a short position in the perpetual and a long position in the spot and close it out much less frequently in order to avoid transaction costs.

In [32]:
df_ticks = pd.DataFrame()
dollar_position_size = 100000
for asset, df in {"perpetual": df_perpetual, "spot": df_spot}.items():
    df = df[["open", "close", "per_return"]].copy()
    df["position_size"] = dollar_position_size / df["close"]
    df.columns = pd.MultiIndex.from_tuples([("adj_open", asset), ("adj_close", asset), ("adj_return", asset), ("position_size", asset)], names=["series", "asset"])
    df_ticks = pd.concat([df_ticks, df], axis=1)
df_ticks[("adj_return", "funding_rate")] = df_funding.fundingRate.shift(-1)
df_ticks[("adj_return", "prior_funding_rate")] = df_funding.fundingRate
df_ticks[("adj_return", "spread")] = df_ticks.adj_close.perpetual / df_ticks.adj_close.spot - 1
df_ticks.index.name = "date"
df_ticks

series               adj_open adj_close adj_return position_size  adj_open  \
asset               perpetual perpetual  perpetual     perpetual      spot   
date                                                                         
2020-05-01 00:00:00   8623.61   8773.25        NaN     11.398285   8620.00   
2020-05-01 08:00:00   8773.07   8730.00  -0.004942     11.454754   8767.18   
2020-05-01 16:00:00   8729.99   8830.52   0.011449     11.324361   8726.88   
2020-05-02 00:00:00   8830.52   8803.32  -0.003085     11.359351   8825.67   
2020-05-02 08:00:00   8804.20   8942.97   0.015739     11.181968   8799.00   
...                       ...       ...        ...           ...       ...   
2021-05-29 00:00:00  35670.99  36180.71   0.014188      2.763904  35661.79   
2021-05-29 08:00:00  36179.68  34452.15  -0.048955      2.902576  36145.00   
2021-05-29 16:00:00  34452.15  34611.94   0.004627      2.889176  34416.26   
2021-05-30 00:00:00  34611.95  35999.99   0.039320      2.777779  34605.15   
2021-05-30 08:00:00  35997.50  35351.73  -0.018171      2.828716  35996.12   

series              adj_close adj_return position_size   adj_return  \
asset                    spot       spot          spot funding_rate   
date                                                                  
2020-05-01 00:00:00   8767.18        NaN     11.406176     0.000179   
2020-05-01 08:00:00   8726.84  -0.004612     11.458902     0.000135   
2020-05-01 16:00:00   8826.96   0.011407     11.328929     0.000100   
2020-05-02 00:00:00   8799.01  -0.003171     11.364915     0.000100   
2020-05-02 08:00:00   8936.41   0.015495     11.190176     0.000101   
...                       ...        ...           ...          ...   
2021-05-29 00:00:00  36145.02   0.013412      2.766633     0.000100   
2021-05-29 08:00:00  34416.27  -0.049010      2.905602     0.000104   
2021-05-29 16:00:00  34605.15   0.005473      2.889743     0.000100   
2021-05-30 00:00:00  35998.33   0.039470      2.777907     0.000100   
2021-05-30 08:00:00  35337.97  -0.018515      2.829817          NaN   

series                                            
asset               prior_funding_rate    spread  
date                                              
2020-05-01 00:00:00           0.000211  0.000692  
2020-05-01 08:00:00           0.000179  0.000362  
2020-05-01 16:00:00           0.000135  0.000403  
2020-05-02 00:00:00           0.000100  0.000490  
2020-05-02 08:00:00           0.000100  0.000734  
...                                ...       ...  
2021-05-29 00:00:00           0.000100  0.000987  
2021-05-29 08:00:00           0.000100  0.001043  
2021-05-29 16:00:00           0.000104  0.000196  
2021-05-30 00:00:00           0.000100  0.000046  
2021-05-30 08:00:00           0.000100  0.000389  

[1184 rows x 11 columns]

In [33]:
strategy_params = dict(
    pair=("spot", "perpetual"),
    df_ticks=df_ticks,
    window=9,
    open_threshold=0.0005,
    close_threshold=0.0002,
    run=True,
    transact_cost_percent = 0.0005,
    closed_positions = [],
)

strategy = utils.Strategy(**strategy_params)
fig = strategy.plot()
fig.show()

In [34]:
df_ticks.loc["2020-05-08":].head(10)

series               adj_open adj_close adj_return position_size adj_open  \
asset               perpetual perpetual  perpetual     perpetual     spot   
date                                                                        
2020-05-08 00:00:00   9994.74   9818.52  -0.017815     10.184834  9986.30   
2020-05-08 08:00:00   9818.61   9949.28   0.013230     10.050979  9810.34   
2020-05-08 16:00:00   9949.61   9807.49  -0.014354     10.196289  9942.07   
2020-05-09 00:00:00   9809.63   9609.65  -0.020379     10.406206  9800.02   
2020-05-09 08:00:00   9608.49   9698.04   0.009156     10.311362  9594.70   
2020-05-09 16:00:00   9697.30   9550.67  -0.015312     10.470470  9688.55   
2020-05-10 00:00:00   9550.25   8807.73  -0.080982     11.353663  9539.10   
2020-05-10 08:00:00   8805.67   8649.62  -0.018114     11.561202  8812.27   
2020-05-10 16:00:00   8649.73   8719.53   0.008050     11.468508  8652.27   
2020-05-11 00:00:00   8723.23   8660.96  -0.006740     11.546064  8722.77   

series              adj_close adj_return position_size   adj_return  \
asset                    spot       spot          spot funding_rate   
date                                                                  
2020-05-08 00:00:00   9810.14  -0.017808     10.193534     0.000340   
2020-05-08 08:00:00   9941.21   0.013272     10.059138     0.000532   
2020-05-08 16:00:00   9800.01  -0.014305     10.204071     0.000420   
2020-05-09 00:00:00   9592.77  -0.021374     10.424518     0.000758   
2020-05-09 08:00:00   9688.62   0.009942     10.321387     0.000580   
2020-05-09 16:00:00   9539.40  -0.015521     10.482840     0.000423   
2020-05-10 00:00:00   8812.28  -0.079284     11.347801     0.000100   
2020-05-10 08:00:00   8650.96  -0.018476     11.559411     0.000100   
2020-05-10 16:00:00   8722.77   0.008267     11.464248     0.000100   
2020-05-11 00:00:00   8664.32  -0.006723     11.541587     0.000100   

series                                            
asset               prior_funding_rate    spread  
date                                              
2020-05-08 00:00:00           0.000161  0.000854  
2020-05-08 08:00:00           0.000340  0.000812  
2020-05-08 16:00:00           0.000532  0.000763  
2020-05-09 00:00:00           0.000420  0.001760  
2020-05-09 08:00:00           0.000758  0.000972  
2020-05-09 16:00:00           0.000580  0.001181  
2020-05-10 00:00:00           0.000423 -0.000516  
2020-05-10 08:00:00           0.000100 -0.000155  
2020-05-10 16:00:00           0.000100 -0.000371  
2020-05-11 00:00:00           0.000100 -0.000388